# Association Rule Mining on Retail Transactions Dataset

In this documentation, after exploring the dataset beforehand, we will begin to apply (some) approach(es) on association rule mining, to see whether the purchase of one product somehow implies the purchase of another product (The lore of Beer and Diaper)

# Table of Contents
* [1. Importing libraries and data preparation](#chapter1)
* [2. Frequent Itemset Mining](#chapter2)
    * [2.1. Apriori Algorithm](#section2_1)
    * [2.2. Enumeration-Tree Algorithm](#section2_2)
    * [2.3. FP-Growth Algorithm](#section2_3)
* [3. Summary and References](#chapter3)

## 1. Importing libraries and data preparation <a id='chapter1'></a>

In [91]:
#Import libraries
import numpy as np
import pandas as pd
from tqdm import tqdm #Show loop progress

In [92]:
#Load dataset
transactions = pd.read_csv('Retail_Transactions_Dataset.csv')
print(f'The dataset has overall {transactions.shape[0]} transactions')
transactions.head()

The dataset has overall 30000 transactions


Transaction_ID                 Date     Customer_Name  \
0      1000000000  2020-12-21 19:42:52   Cheyenne Newman   
1      1000000001  2020-07-06 07:45:16  Emily Fitzgerald   
2      1000000002  2021-10-02 06:28:44      Michael Webb   
3      1000000003  2022-01-10 05:39:02      Kimberly Lin   
4      1000000004  2021-10-13 07:28:47   Cathy Hernandez   

                                             Product  Total_Items  Total_Cost  \
0                                       ['Hair Gel']            6       12.77   
1         ['Tuna', 'Bread', 'Tissues', 'Trash Bags']            5       13.88   
2                         ['Jam', 'Soap', 'Ketchup']            7       47.02   
3                                      ['BBQ Sauce']            9       83.86   
4  ['Hand Sanitizer', 'Bread', 'Extension Cords',...            4       30.55   

   Payment_Method      City         Store_Type  Discount_Applied  \
0      Debit Card  New York  Convenience Store              True   
1      Debit Card   Houston        Supermarket             False   
2      Debit Card     Miami  Convenience Store             False   
3  Mobile Payment   Seattle     Warehouse Club              True   
4      Debit Card   Houston     Warehouse Club             False   

  Customer_Category  Season                   Promotion  
0           Student  Winter                         NaN  
1      Professional    Fall      BOGO (Buy One Get One)  
2       Young Adult  Winter                         NaN  
3    Senior Citizen  Summer  Discount on Selected Items  
4    Senior Citizen  Spring                         NaN

In [93]:
#Take the column consisting of products only
transactions_items = transactions[['Product']]
transactions_items.head()

Product
0                                       ['Hair Gel']
1         ['Tuna', 'Bread', 'Tissues', 'Trash Bags']
2                         ['Jam', 'Soap', 'Ketchup']
3                                      ['BBQ Sauce']
4  ['Hand Sanitizer', 'Bread', 'Extension Cords',...

In [94]:
# Separate the products from the lists
def item_list(itemset):
    items = itemset[1:-1].split(sep = ', ') #Take away the [] brackets from the string and split the items
    items = [item[1:-1] for item in items] #Take away the '' quotes after splitting
    items.sort() # Sort to avoid complexity and make use of the lexicological order later
    return items

item_list("['Jam', 'Soap', 'Ketchup']")

['Jam', 'Ketchup', 'Soap']

In [95]:
# Create a list of given products
product_list = set()
for itemset in transactions_items['Product']:
    items = set(item_list(itemset))
    product_list = product_list | items

print(f'There are in total {len(product_list)} available items:')
print(product_list)

product_list = list(product_list)
product_list.sort()

There are in total 81 available items:
{'Cheese', 'Tissues', 'Orange', 'Ketchup', 'Chicken', 'Shrimp', 'Broom', 'Banana', 'Mop', 'Mayonnaise', 'Baby Wipes', 'Iron', 'Plant Fertilizer', 'Chips', 'Beef', 'Soap', 'Butter', 'Honey', 'Apple', 'Pickles', 'Bread', 'Vacuum Cleaner', 'Toothbrush', 'Bath Towels', 'Rice', 'Deodorant', 'Mustard', 'Cleaning Rags', 'Sponges', 'Hair Gel', 'BBQ Sauce', 'Toothpaste', 'Insect Repellent', 'Feminine Hygiene Products', 'Hand Sanitizer', 'Jam', 'Coffee', 'Cleaning Spray', 'Cereal', 'Onions', 'Ice Cream', 'Dish Soap', 'Pasta', 'Salmon', 'Dishware', 'Cereal Bars', 'Dustpan', 'Trash Bags', 'Air Freshener', 'Toilet Paper', 'Trash Cans', 'Extension Cords', 'Razors', 'Laundry Detergent', 'Power Strips', 'Eggs', 'Lawn Mower', 'Tomatoes', 'Pancake Mix', 'Paper Towels', 'Water', 'Canned Soup', 'Milk', 'Carrots', 'Yogurt', 'Soda', 'Garden Hose', 'Shampoo', 'Shower Gel', 'Shaving Cream', 'Potatoes', 'Spinach', 'Tuna', 'Light Bulbs', 'Syrup', 'Diapers', 'Tea', 'Vinegar

In [96]:
product_list

['Air Freshener',
 'Apple',
 'BBQ Sauce',
 'Baby Wipes',
 'Banana',
 'Bath Towels',
 'Beef',
 'Bread',
 'Broom',
 'Butter',
 'Canned Soup',
 'Carrots',
 'Cereal',
 'Cereal Bars',
 'Cheese',
 'Chicken',
 'Chips',
 'Cleaning Rags',
 'Cleaning Spray',
 'Coffee',
 'Deodorant',
 'Diapers',
 'Dish Soap',
 'Dishware',
 'Dustpan',
 'Eggs',
 'Extension Cords',
 'Feminine Hygiene Products',
 'Garden Hose',
 'Hair Gel',
 'Hand Sanitizer',
 'Honey',
 'Ice Cream',
 'Insect Repellent',
 'Iron',
 'Ironing Board',
 'Jam',
 'Ketchup',
 'Laundry Detergent',
 'Lawn Mower',
 'Light Bulbs',
 'Mayonnaise',
 'Milk',
 'Mop',
 'Mustard',
 'Olive Oil',
 'Onions',
 'Orange',
 'Pancake Mix',
 'Paper Towels',
 'Pasta',
 'Peanut Butter',
 'Pickles',
 'Plant Fertilizer',
 'Potatoes',
 'Power Strips',
 'Razors',
 'Rice',
 'Salmon',
 'Shampoo',
 'Shaving Cream',
 'Shower Gel',
 'Shrimp',
 'Soap',
 'Soda',
 'Spinach',
 'Sponges',
 'Syrup',
 'Tea',
 'Tissues',
 'Toilet Paper',
 'Tomatoes',
 'Toothbrush',
 'Toothpaste',


In [97]:
# Create a function to check the existence of an item in an itemset
def in_set(itemset, item):
    for element in itemset:
        if element == item:
            return True
    return False

for product in product_list:
    transactions_items[product] = transactions_items['Product'].apply(lambda itemset: in_set(item_list(itemset), product))

pd.set_option('display.max_columns', None)
transactions_items.head()

C:\Users\Hello\AppData\Local\Temp\ipykernel_15332\2344140335.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  transactions_items[product] = transactions_items['Product'].apply(lambda itemset: in_set(item_list(itemset), product))
C:\Users\Hello\AppData\Local\Temp\ipykernel_15332\2344140335.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  transactions_items[product] = transactions_items['Product'].apply(lambda itemset: in_set(item_list(itemset), product))
C:\Users\Hello\AppData\Local\Temp\ipykernel_1533

Product  Air Freshener  Apple  \
0                                       ['Hair Gel']          False  False   
1         ['Tuna', 'Bread', 'Tissues', 'Trash Bags']          False  False   
2                         ['Jam', 'Soap', 'Ketchup']          False  False   
3                                      ['BBQ Sauce']          False  False   
4  ['Hand Sanitizer', 'Bread', 'Extension Cords',...          False  False   

   BBQ Sauce  Baby Wipes  Banana  Bath Towels   Beef  Bread  Broom  Butter  \
0      False       False   False        False  False  False  False   False   
1      False       False   False        False  False   True  False   False   
2      False       False   False        False  False  False  False   False   
3       True       False   False        False  False  False  False   False   
4      False       False   False        False  False   True  False   False   

   Canned Soup  Carrots  Cereal  Cereal Bars  Cheese  Chicken  Chips  \
0        False    False   False        False   False    False  False   
1        False    False   False        False   False    False  False   
2        False    False   False        False   False    False  False   
3        False    False   False        False   False    False  False   
4        False    False   False        False   False    False  False   

   Cleaning Rags  Cleaning Spray  Coffee  Deodorant  Diapers  Dish Soap  \
0          False           False   False      False    False      False   
1          False           False   False      False    False      False   
2          False           False   False      False    False      False   
3          False           False   False      False    False      False   
4          False           False   False      False    False      False   

   Dishware  Dustpan   Eggs  Extension Cords  Feminine Hygiene Products  \
0     False    False  False            False                      False   
1     False    False  False            False                      False   
2     False    False  False            False                      False   
3     False    False  False            False                      False   
4     False    False  False             True                      False   

   Garden Hose  Hair Gel  Hand Sanitizer  Honey  Ice Cream  Insect Repellent  \
0        False      True           False  False      False             False   
1        False     False           False  False      False             False   
2        False     False           False  False      False             False   
3        False     False           False  False      False             False   
4        False     False            True  False       True             False   

    Iron  Ironing Board    Jam  Ketchup  Laundry Detergent  Lawn Mower  \
0  False          False  False    False              False       False   
1  False          False  False    False              False       False   
2  False          False   True     True              False       False   
3  False          False  False    False              False       False   
4  False          False  False    False              False       False   

   Light Bulbs  Mayonnaise   Milk    Mop  Mustard  Olive Oil  Onions  Orange  \
0        False       False  False  False    False      False   False   False   
1        False       False  False  False    False      False   False   False   
2        False       False  False  False    False      False   False   False   
3        False       False  False  False    False      False   False   False   
4        False       False  False  False    False      False   False   False   

   Pancake Mix  Paper Towels  Pasta  Peanut Butter  Pickles  Plant Fertilizer  \
0        False         False  False          False    False             False   
1        False         False  False          False    False             False   
2        False         False  False          False    False             False   
3        False         False  False      

With this transformation of the original dataset, we can finally begin to do our data mining process. With the association rule mining problem, there are two phases:
1. Frequent Itemset Mining
2. Generate association Rules

## 2. Frequent Itemset Mining <a id='chapter2'></a>

The first phase among all, is to find out the frequent itemsets with a minimum support (frequency) level.

### 2.1. Apriori Algorithm<a id='section2_1'></a>

For starters, let us begin with __minsup__ = 10% (0.1). We first warm up our intuition by exploring 1-itemsets (itemsets of length 1). Define f_(k) as the set of frequent k-itemsets and c_(k) as the set of candidates to be frequent k-itemsets.

In [98]:
minsup = 0.1
c_1 = []
c_1_length = 0
for item in product_list: #Iterate through all available products
    count = transactions_items[item].sum()
    if count/(transactions.shape[0]) >= minsup:
        c_1.append([item])
        c_1_length+=1
print(c_1)
print(f'There are {c_1_length} 1-itemsets of minsup {minsup}')

[]
There are 0 1-itemsets of minsup 0.1


Oopsies, it seems like we did not find any with the minsup of 0.1. In fact, if we look at the count manually, then at most, one item only appears around 2000 times in the whole transaction database, which is only 6.6% < 10%. Also, we see that most items has the frequecy of around 1000/30000 = 1/30, so let us take this as the minsup.

In [99]:
for item in product_list: #Iterate through all available products
    count = transactions_items[item].sum()
    print(f'{item}: {count}')

Air Freshener: 1088
Apple: 1052
BBQ Sauce: 1074
Baby Wipes: 1066
Banana: 1076
Bath Towels: 1093
Beef: 1110
Bread: 1075
Broom: 1097
Butter: 1136
Canned Soup: 1014
Carrots: 1098
Cereal: 1074
Cereal Bars: 1042
Cheese: 1076
Chicken: 1050
Chips: 1067
Cleaning Rags: 1069
Cleaning Spray: 1092
Coffee: 1031
Deodorant: 1137
Diapers: 1112
Dish Soap: 1119
Dishware: 1081
Dustpan: 1057
Eggs: 1082
Extension Cords: 1104
Feminine Hygiene Products: 1013
Garden Hose: 1147
Hair Gel: 1098
Hand Sanitizer: 1056
Honey: 1092
Ice Cream: 1070
Insect Repellent: 1058
Iron: 1020
Ironing Board: 1124
Jam: 1061
Ketchup: 1077
Laundry Detergent: 1092
Lawn Mower: 1081
Light Bulbs: 1097
Mayonnaise: 1041
Milk: 1087
Mop: 1080
Mustard: 1086
Olive Oil: 1130
Onions: 1134
Orange: 1024
Pancake Mix: 1054
Paper Towels: 1048
Pasta: 1062
Peanut Butter: 1123
Pickles: 1124
Plant Fertilizer: 1087
Potatoes: 1097
Power Strips: 1087
Razors: 1084
Rice: 1090
Salmon: 1100
Shampoo: 1106
Shaving Cream: 1125
Shower Gel: 1046
Shrimp: 1092
Soap: 

Now we define the function formally

In [11]:
def is_candidate(itemset, f_k):
    for i in range(len(itemset)):
        subset = itemset[:i] + itemset[i+1:]
        if subset not in f_k:
            return False
    return True


def generate_candidate(f_k, minsup, k):
    '''
    Find c_(k+1), the candidates to be frequent (k+1)-itemsets, base on the set f_k of frequent k-itemsets given beforehand.
    
    Args:
        f_k: The set of frequent k-itemsets
        minsup: Minimum support (frequency) level to be considered frequent.
        k: length of itemsets in f_k
    '''
    candidates = []
    for i in range(len(f_k)):
        for j in range(i + 1, len(f_k)):
            merge_itemset = sorted(list(set(f_k[i] + f_k[j])))
            if is_candidate(merge_itemset, f_k):
                candidates.append(merge_itemset)
    return candidates
            
    
def apriori(data, minsup):
  """
  Implements the Apriori algorithm to find frequent itemsets in a dataset.

  Args:
      data: A list of transactions (itemsets).
      minsup: Minimum support (frequency) level to be considered frequent.

  Returns:
      A dictionary where keys are frequent itemset sizes (k) and values are lists of frequent itemsets of that size.
  """

  # Initialize frequent 1-itemsets
  f_1 = find_frequent_1_itemsets(data, minsup)  # Assuming find_frequent_1_itemsets is implemented elsewhere

  L = {1: f_1}  # Initialize L with frequent 1-itemsets

  # Iterate over itemset sizes (k)
  for k in tqdm(range(1, len(product_list))):
    # Generate candidate itemsets of size k+1
    candidates = generate_candidate(L[k], minsup, k)
    
    L[k + 1] = list()
    
    for candidate in tqdm(candidates):
        if count_occurences(data, candidate) / len(data) >= minsup:
            L[k+1].append(candidate)
    if len(L[k+1]) == 0:
        break
    print(f'Length of f_{k + 1}: {len(L[k+1])}')
  return L


def find_frequent_1_itemsets(data, minsup):
    result = []
    for item in product_list:
        count = data[item].sum()
        if count / len(data) >= minsup:
            result.append([item])
    return result

def count_occurences(data, candidate):
    filterer = data
    for item in candidate:
        filterer = filterer[filterer[item] == True]
    return len(filterer)

apriori(transactions_items, 0.001)

  1%|█                                                                                  | 1/80 [00:12<16:27, 12.50s/it]

Length of f_2: 2658



  2%|█▎                                                                         | 2468/142395 [00:13<12:56, 180.24it/s]


  3%|██▌                                                                        | 4905/142395 [00:27<13:13, 173.22it/s]


  5%|███▊                                                                       | 7357/142395 [00:41<13:32, 166.29it/s]


...

 96%|█████████████████████████████████████████████████████████████████████▉   | 136308/142395 [12:53<00:39, 152.83it/s]


 97%|███████████████████████████████████████████████████████████████████████  | 138733/142395 [13:07<00:20, 177.14it/s]


 99%|████████████████████████████████████████████████████████████████████████▍| 141270/142395 [13:21<00:07, 156.36it/s]


  1%|▉                                                                              | 1/80 [15:09<19:57:23, 909.41s/it]


{1: [['Air Freshener'],
  ['Apple'],
  ['BBQ Sauce'],
  ['Baby Wipes'],
  ['Banana'],
  ['Bath Towels'],
  ['Beef'],
  ['Bread'],
  ['Broom'],
  ['Butter'],
  ['Canned Soup'],
  ['Carrots'],
  ['Cereal'],
  ['Cereal Bars'],
  ['Cheese'],
  ['Chicken'],
  ['Chips'],
  ['Cleaning Rags'],
  ['Cleaning Spray'],
  ['Coffee'],
  ['Deodorant'],
  ['Diapers'],
  ['Dish Soap'],
  ['Dishware'],
  ['Dustpan'],
  ['Eggs'],
  ['Extension Cords'],
  ['Feminine Hygiene Products'],
  ['Garden Hose'],
  ['Hair Gel'],
  ['Hand Sanitizer'],
  ['Honey'],
  ['Ice Cream'],
  ['Insect Repellent'],
  ['Iron'],
  ['Ironing Board'],
  ['Jam'],
  ['Ketchup'],
  ['Laundry Detergent'],
  ['Lawn Mower'],
  ['Light Bulbs'],
  ['Mayonnaise'],
  ['Milk'],
  ['Mop'],
  ['Mustard'],
  ['Olive Oil'],
  ['Onions'],
  ['Orange'],
  ['Pancake Mix'],
  ['Paper Towels'],
  ['Pasta'],
  ['Peanut Butter'],
  ['Pickles'],
  ['Plant Fertilizer'],
  ['Potatoes'],
  ['Power Strips'],
  ['Razors'],
  ['Rice'],
  ['Salmon'],
  ['Sham

So we see that even when we set the minsup to be very low, it is still impossible to find a frequent 3-itemsets or above. This can be explained as we see that actually the dataset is synthetic, and each item is purchased equally often. At least, now we have an understanding of how Apriori works.

### 2.2. Enumeration-Tree Algorithm<a id='section2_2'></a>

In [10]:
class EnumerationTree:
    def __init__(self, itemset, parent = None):
        self.itemset = itemset
        self.children = []
        self.parent = parent

def generic_enumeration_tree(transactions, minsup = 0.001):
    '''
     Implements the GenericEnumerationTree algorithm.

      Args:
          transactions: A list of transactions (itemsets), represented as lists.
          minsup: Minimum support (frequency) level to be considered frequent.

      Returns:
          The root node of the enumeration tree containing frequent itemsets.
    '''
    
    # Initialize the root node of the tree, containing the empty itemset as the only node
    root = EnumerationTree([])
    
    # Process nodes in each level until we have examined all nodes:
    current_level = [root]
    # While the next level still has at least one node:
    while current_level:
        next_level = []
        for node in current_level:
            candidates = generate_candidate_extensions(node)
            frequent_extensions = filter_frequent_extensions(transactions, minsup, candidates)
            
            for itemset in frequent_extensions:
                child = EnumerationTree(itemset, node)
                node.children.append(child)
                next_level.append(child)
                
        current_level = next_level
    
    return root

def generate_candidate_extensions(node):
    '''
    Generates candidate extensions for a given itemset based on lexicographic order.
    '''
    candidates = []
    if node.parent != None:
        siblings = node.parent.children
        younger_siblings = siblings[siblings.index(node) + 1:]

        for sibling in younger_siblings:
            candidates.append(sorted(list(set(node.itemset) | set(sibling.itemset).difference(set(node.parent.itemset)))))
        return candidates
    for item in product_list:
        candidates.append([item])
    return candidates

def filter_frequent_extensions(transactions, minsup, candidates):
    '''
    Filters frequent extensions from candidates based on minimum support.
    '''
    frequent_extensions = []
    for candidate in candidates:
        count = count_occurences(transactions, candidate)
        print(f'{candidate}: {count}')
        if count / len(transactions) >= minsup:
            frequent_extensions.append(candidate)
    return frequent_extensions

In [14]:
enumTree = generic_enumeration_tree(transactions_items)

['Air Freshener']: 1088
['Apple']: 1052
['BBQ Sauce']: 1074
['Baby Wipes']: 1066
['Banana']: 1076
['Bath Towels']: 1093
['Beef']: 1110
['Bread']: 1075
['Broom']: 1097
['Butter']: 1136
['Canned Soup']: 1014
['Carrots']: 1098
['Cereal']: 1074
['Cereal Bars']: 1042
['Cheese']: 1076
['Chicken']: 1050
['Chips']: 1067
['Cleaning Rags']: 1069
['Cleaning Spray']: 1092
['Coffee']: 1031
['Deodorant']: 1137
['Diapers']: 1112
['Dish Soap']: 1119
['Dishware']: 1081
['Dustpan']: 1057
['Eggs']: 1082
['Extension Cords']: 1104
['Feminine Hygiene Products']: 1013
['Garden Hose']: 1147
['Hair Gel']: 1098
['Hand Sanitizer']: 1056
['Honey']: 1092
['Ice Cream']: 1070
['Insect Repellent']: 1058
['Iron']: 1020
['Ironing Board']: 1124
['Jam']: 1061
['Ketchup']: 1077
['Laundry Detergent']: 1092
['Lawn Mower']: 1081
['Light Bulbs']: 1097
['Mayonnaise']: 1041
['Milk']: 1087
['Mop']: 1080
['Mustard']: 1086
['Olive Oil']: 1130
['Onions']: 1134
['Orange']: 1024
['Pancake Mix']: 1054
['Paper Towels']: 1048
['Pasta']:

['Baby Wipes', 'Ironing Board']: 37
['Baby Wipes', 'Jam']: 36
['Baby Wipes', 'Ketchup']: 36
['Baby Wipes', 'Laundry Detergent']: 28
['Baby Wipes', 'Lawn Mower']: 40
['Baby Wipes', 'Light Bulbs']: 37
['Baby Wipes', 'Mayonnaise']: 32
['Baby Wipes', 'Milk']: 39
['Baby Wipes', 'Mop']: 39
['Baby Wipes', 'Mustard']: 28
['Baby Wipes', 'Olive Oil']: 32
['Baby Wipes', 'Onions']: 40
['Baby Wipes', 'Orange']: 30
['Baby Wipes', 'Pancake Mix']: 31
['Baby Wipes', 'Paper Towels']: 38
['Baby Wipes', 'Pasta']: 37
['Baby Wipes', 'Peanut Butter']: 46
['Baby Wipes', 'Pickles']: 40
['Baby Wipes', 'Plant Fertilizer']: 31
['Baby Wipes', 'Potatoes']: 31
['Baby Wipes', 'Power Strips']: 35
['Baby Wipes', 'Razors']: 24
['Baby Wipes', 'Rice']: 30
['Baby Wipes', 'Salmon']: 41
['Baby Wipes', 'Shampoo']: 34
['Baby Wipes', 'Shaving Cream']: 41
['Baby Wipes', 'Shower Gel']: 44
['Baby Wipes', 'Shrimp']: 39
['Baby Wipes', 'Soap']: 32
['Baby Wipes', 'Soda']: 33
['Baby Wipes', 'Spinach']: 41
['Baby Wipes', 'Sponges']: 33


['Bread', 'Soda']: 44
['Bread', 'Spinach']: 45
['Bread', 'Sponges']: 34
['Bread', 'Syrup']: 28
['Bread', 'Tea']: 40
['Bread', 'Tissues']: 31
['Bread', 'Toilet Paper']: 28
['Bread', 'Tomatoes']: 34
['Bread', 'Toothbrush']: 32
['Bread', 'Toothpaste']: 61
['Bread', 'Trash Bags']: 39
['Bread', 'Trash Cans']: 39
['Bread', 'Tuna']: 38
['Bread', 'Vacuum Cleaner']: 28
['Bread', 'Vinegar']: 32
['Bread', 'Water']: 42
['Bread', 'Yogurt']: 29
['Broom', 'Butter']: 37
['Broom', 'Canned Soup']: 28
['Broom', 'Carrots']: 26
['Broom', 'Cereal']: 40
['Broom', 'Cereal Bars']: 34
['Broom', 'Cheese']: 35
['Broom', 'Chicken']: 34
['Broom', 'Chips']: 42
['Broom', 'Cleaning Rags']: 39
['Broom', 'Cleaning Spray']: 33
['Broom', 'Coffee']: 39
['Broom', 'Deodorant']: 33
['Broom', 'Diapers']: 32
['Broom', 'Dish Soap']: 39
['Broom', 'Dishware']: 45
['Broom', 'Dustpan']: 33
['Broom', 'Eggs']: 33
['Broom', 'Extension Cords']: 25
['Broom', 'Feminine Hygiene Products']: 37
['Broom', 'Garden Hose']: 34
['Broom', 'Hair Ge

['Cereal', 'Dish Soap']: 39
['Cereal', 'Dishware']: 36
['Cereal', 'Dustpan']: 20
['Cereal', 'Eggs']: 27
['Cereal', 'Extension Cords']: 36
['Cereal', 'Feminine Hygiene Products']: 27
['Cereal', 'Garden Hose']: 40
['Cereal', 'Hair Gel']: 42
['Cereal', 'Hand Sanitizer']: 30
['Cereal', 'Honey']: 28
['Cereal', 'Ice Cream']: 41
['Cereal', 'Insect Repellent']: 43
['Cereal', 'Iron']: 26
['Cereal', 'Ironing Board']: 33
['Cereal', 'Jam']: 26
['Cereal', 'Ketchup']: 22
['Cereal', 'Laundry Detergent']: 36
['Cereal', 'Lawn Mower']: 35
['Cereal', 'Light Bulbs']: 36
['Cereal', 'Mayonnaise']: 21
['Cereal', 'Milk']: 37
['Cereal', 'Mop']: 34
['Cereal', 'Mustard']: 39
['Cereal', 'Olive Oil']: 43
['Cereal', 'Onions']: 47
['Cereal', 'Orange']: 25
['Cereal', 'Pancake Mix']: 34
['Cereal', 'Paper Towels']: 32
['Cereal', 'Pasta']: 29
['Cereal', 'Peanut Butter']: 43
['Cereal', 'Pickles']: 34
['Cereal', 'Plant Fertilizer']: 32
['Cereal', 'Potatoes']: 29
['Cereal', 'Power Strips']: 35
['Cereal', 'Razors']: 32
['Ce

['Chips', 'Pasta']: 26
['Chips', 'Peanut Butter']: 41
['Chips', 'Pickles']: 38
['Chips', 'Plant Fertilizer']: 30
['Chips', 'Potatoes']: 41
['Chips', 'Power Strips']: 39
['Chips', 'Razors']: 45
['Chips', 'Rice']: 27
['Chips', 'Salmon']: 35
['Chips', 'Shampoo']: 43
['Chips', 'Shaving Cream']: 36
['Chips', 'Shower Gel']: 29
['Chips', 'Shrimp']: 34
['Chips', 'Soap']: 29
['Chips', 'Soda']: 38
['Chips', 'Spinach']: 34
['Chips', 'Sponges']: 33
['Chips', 'Syrup']: 41
['Chips', 'Tea']: 29
['Chips', 'Tissues']: 35
['Chips', 'Toilet Paper']: 33
['Chips', 'Tomatoes']: 38
['Chips', 'Toothbrush']: 34
['Chips', 'Toothpaste']: 56
['Chips', 'Trash Bags']: 36
['Chips', 'Trash Cans']: 30
['Chips', 'Tuna']: 32
['Chips', 'Vacuum Cleaner']: 28
['Chips', 'Vinegar']: 51
['Chips', 'Water']: 44
['Chips', 'Yogurt']: 23
['Cleaning Rags', 'Cleaning Spray']: 40
['Cleaning Rags', 'Coffee']: 23
['Cleaning Rags', 'Deodorant']: 33
['Cleaning Rags', 'Diapers']: 45
['Cleaning Rags', 'Dish Soap']: 34
['Cleaning Rags', 'Di

...

['Shampoo', 'Toothpaste', 'Tuna']: 1
['Shampoo', 'Toothpaste', 'Vinegar']: 2
['Shampoo', 'Toothpaste', 'Water']: 2
['Shampoo', 'Trash Bags', 'Trash Cans']: 0
['Shampoo', 'Trash Bags', 'Tuna']: 0
['Shampoo', 'Trash Bags', 'Vinegar']: 1
['Shampoo', 'Trash Bags', 'Water']: 3
['Shampoo', 'Trash Cans', 'Tuna']: 0
['Shampoo', 'Trash Cans', 'Vinegar']: 1
['Shampoo', 'Trash Cans', 'Water']: 0
['Shampoo', 'Tuna', 'Vinegar']: 0
['Shampoo', 'Tuna', 'Water']: 3
['Shampoo', 'Vinegar', 'Water']: 2
['Shaving Cream', 'Shower Gel', 'Shrimp']: 0
['Shaving Cream', 'Shower Gel', 'Soda']: 1
['Shaving Cream', 'Shower Gel', 'Spinach']: 0
['Shaving Cream', 'Shower Gel', 'Sponges']: 2
['Shaving Cream', 'Shower Gel', 'Tea']: 1
['Shaving Cream', 'Shower Gel', 'Tissues']: 1
['Shaving Cream', 'Shower Gel', 'Toilet Paper']: 1
['Shaving Cream', 'Shower Gel', 'Tomatoes']: 0
['Shaving Cream', 'Shower Gel', 'Toothbrush']: 0
['Shaving Cream', 'Shower Gel', 'Toothpaste']: 0
['Shaving Cream', 'Shower Gel', 'Trash Bags']: 

['Shower Gel', 'Soda', 'Tea']: 2
['Shower Gel', 'Soda', 'Tissues']: 3
['Shower Gel', 'Soda', 'Toilet Paper']: 1
['Shower Gel', 'Soda', 'Tomatoes']: 2
['Shower Gel', 'Soda', 'Toothbrush']: 1
['Shower Gel', 'Soda', 'Toothpaste']: 2
['Shower Gel', 'Soda', 'Trash Bags']: 1
['Shower Gel', 'Soda', 'Trash Cans']: 1
['Shower Gel', 'Soda', 'Tuna']: 3
['Shower Gel', 'Soda', 'Vacuum Cleaner']: 2
['Shower Gel', 'Soda', 'Vinegar']: 0
['Shower Gel', 'Soda', 'Water']: 0
['Shower Gel', 'Soda', 'Yogurt']: 3
['Shower Gel', 'Spinach', 'Sponges']: 0
['Shower Gel', 'Spinach', 'Syrup']: 0
['Shower Gel', 'Spinach', 'Tea']: 0
['Shower Gel', 'Spinach', 'Tissues']: 0
['Shower Gel', 'Spinach', 'Toilet Paper']: 1
['Shower Gel', 'Spinach', 'Tomatoes']: 1
['Shower Gel', 'Spinach', 'Toothbrush']: 1
['Shower Gel', 'Spinach', 'Toothpaste']: 1
['Shower Gel', 'Spinach', 'Trash Bags']: 0
['Shower Gel', 'Spinach', 'Trash Cans']: 1
['Shower Gel', 'Spinach', 'Tuna']: 1
['Shower Gel', 'Spinach', 'Vacuum Cleaner']: 3
['Shower

['Soap', 'Toilet Paper', 'Tuna']: 0
['Soap', 'Toilet Paper', 'Vacuum Cleaner']: 2
['Soap', 'Toilet Paper', 'Vinegar']: 1
['Soap', 'Toilet Paper', 'Yogurt']: 0
['Soap', 'Tomatoes', 'Toothbrush']: 1
['Soap', 'Tomatoes', 'Toothpaste']: 2
['Soap', 'Tomatoes', 'Trash Bags']: 1
['Soap', 'Tomatoes', 'Tuna']: 1
['Soap', 'Tomatoes', 'Vacuum Cleaner']: 0
['Soap', 'Tomatoes', 'Vinegar']: 0
['Soap', 'Tomatoes', 'Yogurt']: 1
['Soap', 'Toothbrush', 'Toothpaste']: 2
['Soap', 'Toothbrush', 'Trash Bags']: 1
['Soap', 'Toothbrush', 'Tuna']: 0
['Soap', 'Toothbrush', 'Vacuum Cleaner']: 1
['Soap', 'Toothbrush', 'Vinegar']: 0
['Soap', 'Toothbrush', 'Yogurt']: 0
['Soap', 'Toothpaste', 'Trash Bags']: 3
['Soap', 'Toothpaste', 'Tuna']: 1
['Soap', 'Toothpaste', 'Vacuum Cleaner']: 1
['Soap', 'Toothpaste', 'Vinegar']: 0
['Soap', 'Toothpaste', 'Yogurt']: 1
['Soap', 'Trash Bags', 'Tuna']: 2
['Soap', 'Trash Bags', 'Vacuum Cleaner']: 1
['Soap', 'Trash Bags', 'Vinegar']: 1
['Soap', 'Trash Bags', 'Yogurt']: 1
['Soap', 'T

['Sponges', 'Toothpaste', 'Trash Bags']: 5
['Sponges', 'Toothpaste', 'Trash Cans']: 2
['Sponges', 'Toothpaste', 'Vinegar']: 3
['Sponges', 'Toothpaste', 'Water']: 1
['Sponges', 'Toothpaste', 'Yogurt']: 2
['Sponges', 'Trash Bags', 'Trash Cans']: 3
['Sponges', 'Trash Bags', 'Vinegar']: 1
['Sponges', 'Trash Bags', 'Water']: 0
['Sponges', 'Trash Bags', 'Yogurt']: 0
['Sponges', 'Trash Cans', 'Vinegar']: 1
['Sponges', 'Trash Cans', 'Water']: 1
['Sponges', 'Trash Cans', 'Yogurt']: 2
['Sponges', 'Vinegar', 'Water']: 0
['Sponges', 'Vinegar', 'Yogurt']: 0
['Sponges', 'Water', 'Yogurt']: 1
['Syrup', 'Tea', 'Tissues']: 1
['Syrup', 'Tea', 'Toilet Paper']: 4
['Syrup', 'Tea', 'Tomatoes']: 2
['Syrup', 'Tea', 'Toothpaste']: 1
['Syrup', 'Tea', 'Trash Bags']: 2
['Syrup', 'Tea', 'Trash Cans']: 3
['Syrup', 'Tea', 'Tuna']: 2
['Syrup', 'Tea', 'Vacuum Cleaner']: 2
['Syrup', 'Tea', 'Vinegar']: 3
['Syrup', 'Tea', 'Water']: 1
['Syrup', 'Tea', 'Yogurt']: 2
['Syrup', 'Tissues', 'Toilet Paper']: 0
['Syrup', 'Tissues

['Toothbrush', 'Vacuum Cleaner', 'Yogurt']: 2
['Toothbrush', 'Vinegar', 'Water']: 0
['Toothbrush', 'Vinegar', 'Yogurt']: 0
['Toothbrush', 'Water', 'Yogurt']: 0
['Toothpaste', 'Trash Bags', 'Trash Cans']: 3
['Toothpaste', 'Trash Bags', 'Tuna']: 3
['Toothpaste', 'Trash Bags', 'Vacuum Cleaner']: 1
['Toothpaste', 'Trash Bags', 'Vinegar']: 2
['Toothpaste', 'Trash Bags', 'Water']: 1
['Toothpaste', 'Trash Bags', 'Yogurt']: 4
['Toothpaste', 'Trash Cans', 'Tuna']: 1
['Toothpaste', 'Trash Cans', 'Vacuum Cleaner']: 4
['Toothpaste', 'Trash Cans', 'Vinegar']: 2
['Toothpaste', 'Trash Cans', 'Water']: 1
['Toothpaste', 'Trash Cans', 'Yogurt']: 4
['Toothpaste', 'Tuna', 'Vacuum Cleaner']: 0
['Toothpaste', 'Tuna', 'Vinegar']: 4
['Toothpaste', 'Tuna', 'Water']: 4
['Toothpaste', 'Tuna', 'Yogurt']: 4
['Toothpaste', 'Vacuum Cleaner', 'Vinegar']: 1
['Toothpaste', 'Vacuum Cleaner', 'Water']: 2
['Toothpaste', 'Vacuum Cleaner', 'Yogurt']: 2
['Toothpaste', 'Vinegar', 'Water']: 2
['Toothpaste', 'Vinegar', 'Yogurt'

Cross-referencing with Apriori, we find that the results are similar, this is another approach using enumeration tree, where we can prune the joins better in comparison with Apriori

### 2.3. FP-Growth Algorithm <a id='section2_3'></a>

In the two algorithms above, with each new candidate itemset found, we have to scan the database all over again. Here, we try an attempt that can simplify the process, where the database does not have to be repetitively scanned.

In [100]:
# Create a map containing frequent items only
def frequent_items_count(transactions, minsup = 0.001):
    result = dict()
    for item in product_list:
        count = transactions_items[item].sum()
        if count/len(transactions) >= minsup:
            result[item] = count
    return result

#Filter transactions that contains infrequent items:
def filter_transactions(transactions, minsup = 0.001):
    transaction_list = []
    frequent_items = [key for key in frequent_items_count(transactions, minsup).keys()]
    for itemset in transactions['Product']:
        items = item_list(itemset)
        to_remove = False
        for item in items:
            if item not in frequent_items:
                to_remove = True
                break
        if to_remove == False:
            transaction_list.append(items)
    return transaction_list

In [101]:
frequent_items_dictionary = frequent_items_count(transactions_items)
frequent_items_dictionary

{'Air Freshener': 1088,
 'Apple': 1052,
 'BBQ Sauce': 1074,
 'Baby Wipes': 1066,
 'Banana': 1076,
 'Bath Towels': 1093,
 'Beef': 1110,
 'Bread': 1075,
 'Broom': 1097,
 'Butter': 1136,
 'Canned Soup': 1014,
 'Carrots': 1098,
 'Cereal': 1074,
 'Cereal Bars': 1042,
 'Cheese': 1076,
 'Chicken': 1050,
 'Chips': 1067,
 'Cleaning Rags': 1069,
 'Cleaning Spray': 1092,
 'Coffee': 1031,
 'Deodorant': 1137,
 'Diapers': 1112,
 'Dish Soap': 1119,
 'Dishware': 1081,
 'Dustpan': 1057,
 'Eggs': 1082,
 'Extension Cords': 1104,
 'Feminine Hygiene Products': 1013,
 'Garden Hose': 1147,
 'Hair Gel': 1098,
 'Hand Sanitizer': 1056,
 'Honey': 1092,
 'Ice Cream': 1070,
 'Insect Repellent': 1058,
 'Iron': 1020,
 'Ironing Board': 1124,
 'Jam': 1061,
 'Ketchup': 1077,
 'Laundry Detergent': 1092,
 'Lawn Mower': 1081,
 'Light Bulbs': 1097,
 'Mayonnaise': 1041,
 'Milk': 1087,
 'Mop': 1080,
 'Mustard': 1086,
 'Olive Oil': 1130,
 'Onions': 1134,
 'Orange': 1024,
 'Pancake Mix': 1054,
 'Paper Towels': 1048,
 'Pasta': 

In [124]:
filtered_transactions = filter_transactions(transactions_items)
filtered_transactions = [list(set(transaction)) for transaction in filtered_transactions]

In [125]:
filtered_transactions = [sorted(itemset, key=lambda x: frequent_items_dictionary[x], reverse=True) for itemset in filtered_transactions]
filtered_transactions

[['Hair Gel'],
 ['Tuna', 'Trash Bags', 'Tissues', 'Bread'],
 ['Soap', 'Ketchup', 'Jam'],
 ['BBQ Sauce'],
 ['Extension Cords', 'Bread', 'Ice Cream', 'Hand Sanitizer'],
 ['Banana', 'Baby Wipes', 'Paper Towels', 'Shower Gel'],
 ['Tuna', 'Cereal'],
 ['Tuna', 'Extension Cords', 'Eggs', 'Iron'],
 ['Pickles', 'Banana'],
 ['Razors', 'Lawn Mower', 'Ketchup'],
 ['Soda', 'Shrimp'],
 ['Soap', 'Shower Gel', 'Mayonnaise', 'Vacuum Cleaner'],
 ['Soda', 'Lawn Mower', 'BBQ Sauce'],
 ['Deodorant', 'Ironing Board', 'Laundry Detergent', 'Cereal'],
 ['Lawn Mower', 'Tea'],
 ['Syrup'],
 ['Spinach', 'Peanut Butter', 'Mustard', 'Cleaning Rags', 'Tea'],
 ['Tuna', 'Potatoes', 'Bath Towels'],
 ['Yogurt', 'Eggs', 'Syrup'],
 ['Eggs'],
 ['Toothpaste', 'Peanut Butter', 'Razors', 'Eggs', 'Cheese'],
 ['Dish Soap', 'Shrimp', 'Milk'],
 ['Water', 'Laundry Detergent', 'Bread', 'Cereal'],
 ['Soda', 'Laundry Detergent', 'Insect Repellent'],
 ['Toothpaste', 'Hair Gel', 'Plant Fertilizer', 'Dishware', 'Apple'],
 ['Extension Cor

In [132]:
# Create FP-Tree:

class FP_Tree:
    def __init__(self, pair=('null', 30000), children=None):
        self.pair = pair
        self.children = []
    # Add a transaction to the tree 
    
    def add_path(self, transaction):
        if len(transaction) == 0:
            pass
        else:
    # Call out the directly connected items to the current nodes
            suffixes = [child.pair[0] for child in self.children]
            next_child = self
            found = False  # Flag to track if a matching item is found

    # Iterate through children and stop if a match is found
            for index, child_node in enumerate(self.children):
                if child_node.pair[0] == transaction[0]:
                    item, count = child_node.pair[0], child_node.pair[1]
                    self.children[index].pair = (item, count + 1)
                    next_child = child_node
                    found = True
                    break  # Exit the loop if a match is found

    # If no match found, create a new child node
                
            if not found:
                pair = (transaction[0], 1)
                new_child = FP_Tree(pair)
                self.children.append(new_child)
                next_child = new_child
                
            next_child.add_path(transaction[1:])
    def show_paths(self, current_path, all_paths):
        current_path.append(self.pair)
        if not self.children:
            all_paths.append(current_path.copy())
            return
        for child in self.children:
            child.show_paths(current_path, all_paths)
            current_path.pop()
    
    def generate_conditional_pattern_base(self, current_path, item, all_patterns):
        current_path.append(self.pair[0])
        if current_path[-1] == item:
            if self.pair[1] >
            all_patterns.append((current_path.copy(), self.pair[1]))
        if not self.children:
            return
        for child in self.children:
            child.generate_conditional_pattern_base(current_path, item, all_patterns)
            current_path.pop()
        
    
root = FP_Tree()
count = 1
for transaction in filtered_transactions:
    root.add_path(transaction)

all_paths = []
root.show_paths([], all_paths)
all_paths

[[('null', 30000), ('Hair Gel', 493), ('Feminine Hygiene Products', 1)],
 [('null', 30000),
  ('Hair Gel', 493),
  ('Insect Repellent', 8),
  ('Shower Gel', 1),
  ('Orange', 1)],
 [('null', 30000),
  ('Hair Gel', 493),
  ('Insect Repellent', 8),
  ('Paper Towels', 2)],
 [('null', 30000),
  ('Hair Gel', 493),
  ('Insect Repellent', 8),
  ('Hand Sanitizer', 1)],
 [('null', 30000),
  ('Hair Gel', 493),
  ('Insect Repellent', 8),
  ('Iron', 1),
  ('Canned Soup', 1)],
 [('null', 30000),
  ('Hair Gel', 493),
  ('Potatoes', 17),
  ('Razors', 1),
  ('Dishware', 1),
  ('Dustpan', 1)],
 [('null', 30000),
  ('Hair Gel', 493),
  ('Potatoes', 17),
  ('Shrimp', 1),
  ('Lawn Mower', 1),
  ('Chicken', 1)],
 [('null', 30000),
  ('Hair Gel', 493),
  ('Potatoes', 17),
  ('Toilet Paper', 1),
  ('Trash Cans', 1),
  ('Dishware', 1)],
 [('null', 30000), ('Hair Gel', 493), ('Potatoes', 17), ('Eggs', 1)],
 [('null', 30000), ('Hair Gel', 493), ('Potatoes', 17), ('Jam', 1)],
 [('null', 30000),
  ('Hair Gel', 493

In [133]:
test = filtered_transactions[:6]
test_root = FP_Tree()
for transaction in test:
    test_root.add_path(transaction)
all_paths = []    
test_root.show_paths([], all_paths)
all_paths
all_patterns = []
test_root.generate_conditional_pattern_base([], 'Bread', all_patterns)
all_patterns

[(['null', 'Tuna', 'Trash Bags', 'Tissues', 'Bread'], 1),
 (['null', 'Extension Cords', 'Bread'], 1)]

In [127]:
all_paths

[[('null', 30000), ('Hair Gel', 1)],
 [('null', 30000),
  ('Tuna', 1),
  ('Trash Bags', 1),
  ('Tissues', 1),
  ('Bread', 1)],
 [('null', 30000), ('Soap', 1), ('Ketchup', 1), ('Jam', 1)],
 [('null', 30000), ('BBQ Sauce', 1)],
 [('null', 30000),
  ('Extension Cords', 1),
  ('Bread', 1),
  ('Ice Cream', 1),
  ('Hand Sanitizer', 1)],
 [('null', 30000),
  ('Banana', 1),
  ('Baby Wipes', 1),
  ('Paper Towels', 1),
  ('Shower Gel', 1)]]

In [128]:
test

[['Hair Gel'],
 ['Tuna', 'Trash Bags', 'Tissues', 'Bread'],
 ['Soap', 'Ketchup', 'Jam'],
 ['BBQ Sauce'],
 ['Extension Cords', 'Bread', 'Ice Cream', 'Hand Sanitizer'],
 ['Banana', 'Baby Wipes', 'Paper Towels', 'Shower Gel']]

Now we can call the the generate_conditional_pattern_base function recursively to give out the patterns containing given suffixes that have support greater than or equal to minsup, until all patterns are found

## 3. Summary and References <a id='chapter3'></a>

So, we managed to implement three different approaches for association rule mining on the retail transactions dataset and have a hold of how they work basically. In the next part, we will discover more aspects to the problem of association rule mining, like evaluating rules using certain metrics

References:
- Data Mining: The Textbook, Charu C. Aggarwal
- Frequent Pattern Growth Algorithm: https://www.geeksforgeeks.org/frequent-pattern-growth-algorithm/
- Mining the Frequent Pattern Tree: https://dm.cs.tu-dortmund.de/en/mlbits/frequent-pattern-fptree-mining/#ref-DBLP:conf/pakdd/BonchiG04